In [1]:
import pandas as pd
import numpy as np
import folium
import json

In [2]:
#Read in HCI databuild with missings filled in
cahouseurl = 'https://github.com/crsalviati/CA_Housing/raw/master/Code/ca_house_missing_filled.txt'
cahouse = pd.read_csv(cahouseurl, converters={'geotypevalue':str,'county_fips':str})

In [3]:
#Read in CA County geojson file
import urllib2

req = urllib2.Request("https://raw.githubusercontent.com/crsalviati/CA_Housing/master/ca_counties.json")
opener = urllib2.build_opener()
f = opener.open(req)
county_geo = json.loads(f.read())
print county_geo
#print json['unit']

#county_geo = (r'https://raw.githubusercontent.com/crsalviati/CA_Housing/master/ca_counties.json')
#with open('https://raw.githubusercontent.com/crsalviati/CA_Housing/master/ca_counties.json') as counties:
#    countygeo = json.load(counties)
#countygeo['features'][0]

{u'type': u'FeatureCollection', u'features': [{u'geometry': {u'type': u'MultiPolygon', u'coordinates': [[[[-124.194502, 40.961703], [-124.182694, 41.001312999999996], [-124.204984, 41.013638], [-124.227079, 41.046622], [-124.231202, 41.065501], [-124.249588, 41.099025], [-124.24916400000001, 41.120157], [-124.252474, 41.134074999999996], [-124.247236, 41.152817], [-124.237625, 41.165959], [-124.21941799999999, 41.177687], [-124.195532, 41.184582], [-124.176367, 41.237148], [-124.173316, 41.260995], [-124.160704, 41.289293], [-124.163398, 41.293169], [-124.192328, 41.29199], [-124.220032, 41.302994], [-124.23821, 41.321446], [-124.24242, 41.3433], [-124.238191, 41.358705], [-124.231087, 41.368856], [-124.206515, 41.384718], [-124.176556, 41.390352], [-124.154195, 41.387628], [-124.139973, 41.381820999999995], [-124.133231, 41.432311], [-124.136906, 41.446822999999995], [-124.136561, 41.464452], [-123.770551, 41.464193], [-123.770239, 41.380776], [-123.50117, 41.382567], [-123.474085, 41

In [4]:
#Read in file with list of all CA Counties (some counties aren't represented in the data, but need to have 
#them in there with Nan values or maps don't work)
countynameurl = 'https://raw.githubusercontent.com/crsalviati/CA_Housing/master/county_names.txt'
countyname = pd.read_csv(countynameurl, sep='\n')

In [5]:
#zri_sqft: collapse to get population weighted avg by county then merge with county names from above
zri = cahouse[['zri_sqft', 'county', 'pop2010']]
zri = zri.dropna()
zri.county = zri.county + " County, CA"
zri['zri_pop'] = zri.zri_sqft*zri.pop2010
zri = zri.groupby(zri.county).sum()
zri['zri_county'] = zri.zri_pop/zri.pop2010
zri = zri.drop(['zri_sqft', 'pop2010', 'zri_pop'], axis=1)
zri.reset_index(level=0, inplace=True)
zri = pd.merge(zri, countyname, on='county', how='outer')
zri.head()

county  zri_county
0    Alameda County, CA    1.413412
1     Amador County, CA    0.949179
2      Butte County, CA    0.947340
3  Calaveras County, CA    0.946310
4     Colusa County, CA    0.845439

In [44]:
#Choropleth - zri_sqft
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=zri,
                columns=['county', 'zri_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[0.6,0.9,1.05,1.2,1.8,2.5],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [7]:
#hval_sqft: collapse to get population weighted avg by county then merge with county names from above
hval = cahouse[['hval_sqft', 'county', 'pop2010']]
hval = hval.dropna()
hval.county = hval.county + " County, CA"
hval['hval_pop'] = hval.hval_sqft*hval.pop2010
hval = hval.groupby(hval.county).sum()
hval['hval_county'] = hval.hval_pop/hval.pop2010
hval = hval.drop(['hval_sqft', 'pop2010', 'hval_pop'], axis=1)
hval.reset_index(level=0, inplace=True)
hval = pd.merge(hval, countyname, on='county', how='outer')
hval.head()

county  hval_county
0       Alameda County, CA   297.090233
1        Amador County, CA   140.797675
2         Butte County, CA   134.576400
3     Calaveras County, CA   130.616714
4  Contra Costa County, CA   216.854708

In [8]:
#Choropleth - hval_sqft
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=hval,
                columns=['county', 'hval_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[50,100,150,200,300,450],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [9]:
#ozone: collapse to get population weighted avg by county then merge with county names from above
ozone = cahouse[['ozone', 'county', 'pop2010']]
ozone = ozone.dropna()
ozone.county = ozone.county + " County, CA"
ozone['ozone_pop'] = ozone.ozone*ozone.pop2010
ozone = ozone.groupby(ozone.county).sum()
ozone['ozone_county'] = ozone.ozone_pop/ozone.pop2010
ozone = ozone.drop(['ozone', 'pop2010', 'ozone_pop'], axis=1)
ozone.reset_index(level=0, inplace=True)
ozone = pd.merge(ozone, countyname, on='county', how='outer')
ozone.head()

county  ozone_county
0    Alameda County, CA      0.459792
1     Amador County, CA     11.791826
2      Butte County, CA      5.605761
3  Calaveras County, CA      8.086922
4     Colusa County, CA      0.494288

In [10]:
#Choropleth - ozone
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=ozone,
                columns=['county', 'ozone_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[0,5,10,20,30,40],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [11]:
#gini_index: collapse to get population weighted avg by county then merge with county names from above
gini_index = cahouse[['gini_index', 'county', 'pop2010']]
gini_index = gini_index.dropna()
gini_index.county = gini_index.county + " County, CA"
gini_index['gini_index_pop'] = gini_index.gini_index*gini_index.pop2010
gini_index = gini_index.groupby(gini_index.county).sum()
gini_index['gini_index_county'] = gini_index.gini_index_pop/gini_index.pop2010
gini_index = gini_index.drop(['gini_index', 'pop2010', 'gini_index_pop'], axis=1)
gini_index.reset_index(level=0, inplace=True)
gini_index = pd.merge(gini_index, countyname, on='county', how='outer')
gini_index.head()

county  gini_index_county
0    Alameda County, CA           0.436311
1     Amador County, CA           0.372834
2      Butte County, CA           0.444823
3  Calaveras County, CA           0.389385
4     Colusa County, CA           0.382920

In [48]:
#Choropleth - gini_index
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=gini_index,
                columns=['county', 'gini_index_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[0.37,0.41,0.425,0.44,0.47,0.5],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [13]:
#median_hh_income: collapse to get population weighted avg by county then merge with county names from above
median_hh_income = cahouse[['median_hh_income', 'county', 'pop2010']]
median_hh_income = median_hh_income.dropna()
median_hh_income.county = median_hh_income.county + " County, CA"
median_hh_income['median_hh_income_pop'] = median_hh_income.median_hh_income*median_hh_income.pop2010
median_hh_income = median_hh_income.groupby(median_hh_income.county).sum()
median_hh_income['median_hh_income_county'] = median_hh_income.median_hh_income_pop/median_hh_income.pop2010
median_hh_income = median_hh_income.drop(['median_hh_income', 'pop2010', 'median_hh_income_pop'], axis=1)
median_hh_income.reset_index(level=0, inplace=True)
median_hh_income = pd.merge(median_hh_income, countyname, on='county', how='outer')
median_hh_income.head()

county  median_hh_income_county
0    Alameda County, CA             73293.041556
1     Amador County, CA             58169.276976
2      Butte County, CA             42387.723845
3  Calaveras County, CA             52807.320921
4     Colusa County, CA             44648.649979

In [14]:
#Choropleth - median_hh_income
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=median_hh_income,
                columns=['county', 'median_hh_income_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                legend_name='Rental Price Per Sqft (Index)')
counties

/Applications/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:7: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [15]:
#p_hs_edatt: collapse to get population weighted avg by county then merge with county names from above
p_hs_edatt = cahouse[['p_hs_edatt', 'county', 'pop2010']]
p_hs_edatt = p_hs_edatt.dropna()
p_hs_edatt.county = p_hs_edatt.county + " County, CA"
p_hs_edatt['p_hs_edatt_pop'] = p_hs_edatt.p_hs_edatt*p_hs_edatt.pop2010
p_hs_edatt = p_hs_edatt.groupby(p_hs_edatt.county).sum()
p_hs_edatt['p_hs_edatt_county'] = p_hs_edatt.p_hs_edatt_pop/p_hs_edatt.pop2010
p_hs_edatt = p_hs_edatt.drop(['p_hs_edatt', 'pop2010', 'p_hs_edatt_pop'], axis=1)
p_hs_edatt.reset_index(level=0, inplace=True)
p_hs_edatt = pd.merge(p_hs_edatt, countyname, on='county', how='outer')
p_hs_edatt.head()

county  p_hs_edatt_county
0    Alameda County, CA          86.213175
1     Amador County, CA          83.236640
2      Butte County, CA          88.154585
3  Calaveras County, CA          90.552596
4     Colusa County, CA          64.576937

In [16]:
#Choropleth - p_hs_edatt
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=p_hs_edatt,
                columns=['county', 'p_hs_edatt_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[60,70,80,85,90,95],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [17]:
#unemp_rate: collapse to get population weighted avg by county then merge with county names from above
unemp_rate = cahouse[['unemp_rate', 'county', 'pop2010']]
unemp_rate = unemp_rate.dropna()
unemp_rate.county = unemp_rate.county + " County, CA"
unemp_rate['unemp_rate_pop'] = unemp_rate.unemp_rate*unemp_rate.pop2010
unemp_rate = unemp_rate.groupby(unemp_rate.county).sum()
unemp_rate['unemp_rate_county'] = unemp_rate.unemp_rate_pop/unemp_rate.pop2010
unemp_rate = unemp_rate.drop(['unemp_rate', 'pop2010', 'unemp_rate_pop'], axis=1)
unemp_rate.reset_index(level=0, inplace=True)
unemp_rate = pd.merge(unemp_rate, countyname, on='county', how='outer')
unemp_rate.head()

county  unemp_rate_county
0    Alameda County, CA           8.406195
1     Amador County, CA           8.099000
2      Butte County, CA          10.767116
3  Calaveras County, CA           6.723056
4     Colusa County, CA          15.893981

In [18]:
#Choropleth - unemp_rate
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=unemp_rate,
                columns=['county', 'unemp_rate_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[4,7,9,11,14,17],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [19]:
#poverty_all: collapse to get population weighted avg by county then merge with county names from above
poverty_all = cahouse[['poverty_all', 'county', 'pop2010']]
poverty_all = poverty_all.dropna()
poverty_all.county = poverty_all.county + " County, CA"
poverty_all['poverty_all_pop'] = poverty_all.poverty_all*poverty_all.pop2010
poverty_all = poverty_all.groupby(poverty_all.county).sum()
poverty_all['poverty_all_county'] = poverty_all.poverty_all_pop/poverty_all.pop2010
poverty_all = poverty_all.drop(['poverty_all', 'pop2010', 'poverty_all_pop'], axis=1)
poverty_all.reset_index(level=0, inplace=True)
poverty_all = pd.merge(poverty_all, countyname, on='county', how='outer')
poverty_all.head()

county  poverty_all_county
0    Alameda County, CA           11.315092
1     Amador County, CA            8.282519
2      Butte County, CA           18.844563
3  Calaveras County, CA            7.811714
4     Colusa County, CA           15.022950

In [20]:
#Choropleth - poverty_all
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=poverty_all,
                columns=['county', 'poverty_all_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[5,10,14,18,22,30],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [21]:
#alc_on: collapse to get population weighted avg by county then merge with county names from above
alc_on = cahouse[['alc_on', 'county', 'pop2010']]
alc_on = alc_on.dropna()
alc_on.county = alc_on.county + " County, CA"
alc_on['alc_on_pop'] = alc_on.alc_on*alc_on.pop2010
alc_on = alc_on.groupby(alc_on.county).sum()
alc_on['alc_on_county'] = alc_on.alc_on_pop/alc_on.pop2010
alc_on = alc_on.drop(['alc_on', 'pop2010', 'alc_on_pop'], axis=1)
alc_on.reset_index(level=0, inplace=True)
alc_on = pd.merge(alc_on, countyname, on='county', how='outer')
alc_on.head()

county  alc_on_county
0    Alameda County, CA      40.566635
1     Amador County, CA      31.534929
2      Butte County, CA      33.664114
3  Calaveras County, CA      19.975878
4     Colusa County, CA      31.730633

In [22]:
#Choropleth - alc_on
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=alc_on,
                columns=['county', 'alc_on_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[20,25,30,40,50,80],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [31]:
#hh_fam: collapse to get population weighted avg by county then merge with county names from above
hh_fam = cahouse[['hh_fam', 'county', 'pop2010']]
hh_fam = hh_fam.dropna()
hh_fam.county = hh_fam.county + " County, CA"
hh_fam['hh_fam_pop'] = hh_fam.hh_fam*hh_fam.pop2010
hh_fam = hh_fam.groupby(hh_fam.county).sum()
hh_fam['hh_fam_county'] = hh_fam.hh_fam_pop/hh_fam.pop2010
hh_fam = hh_fam.drop(['hh_fam', 'pop2010', 'hh_fam_pop'], axis=1)
hh_fam.reset_index(level=0, inplace=True)
hh_fam = pd.merge(hh_fam, countyname, on='county', how='outer')
hh_fam.head()

county  hh_fam_county
0    Alameda County, CA      65.019843
1     Amador County, CA      66.773008
2      Butte County, CA      58.008858
3  Calaveras County, CA      67.902171
4     Colusa County, CA      74.303364

In [49]:
#Choropleth - hh_fam
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=hh_fam,
                columns=['county', 'hh_fam_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[45,58,65,70,75,80],
                legend_name='Rental Price Per Sqft (Index)')
counties

In [50]:
#nocar: collapse to get population weighted avg by county then merge with county names from above
nocar = cahouse[['nocar', 'county', 'pop2010']]
nocar = nocar.dropna()
nocar.county = nocar.county + " County, CA"
nocar['nocar_pop'] = nocar.nocar*nocar.pop2010
nocar = nocar.groupby(nocar.county).sum()
nocar['nocar_county'] = nocar.nocar_pop/nocar.pop2010
nocar = nocar.drop(['nocar', 'pop2010', 'nocar_pop'], axis=1)
nocar.reset_index(level=0, inplace=True)
nocar = pd.merge(nocar, countyname, on='county', how='outer')
nocar.head()

county  nocar_county
0    Alameda County, CA     16.674070
1     Amador County, CA      3.642395
2      Butte County, CA      8.859048
3  Calaveras County, CA      6.110823
4     Colusa County, CA      4.725070

In [61]:
#Choropleth - nocar
counties = folium.Map(location=[37.5, -120], zoom_start=6)
counties.choropleth(geo_str=county_geo, data=nocar,
                columns=['county', 'nocar_county'],
                key_on='properties.name',
                fill_color='YlOrRd', fill_opacity=0.8, line_opacity=0.2,
                threshold_scale=[0,4,8,12,25,50],
                legend_name='Rental Price Per Sqft (Index)')
counties